# Matrix multiplication

In this benchmark we will compare the performance of ironArray, NumPy, Zarr+Dask, HDF5+Dask and TileDB+Dask when calculating a matrix product. We will first set up the optimized arrays from the corresponding [Matrix Multiplication tutorial](../tutorials/10.Matrix_Multiplication.html), and then compute the matrix multiplication.    It is important to stress that we are using defaults for every library, which are typically fine tuned for general performance; this is a pretty fair way to compare them without spending long time optimizing for every one.

We will first set up the arrays with the same chunk shape, and then compute the matrix multiplication.

In [1]:
import iarray as ia
import numpy as np
import os
import tiledb
import zarr
import dask.array as da
import h5py
import hdf5plugin as h5plugin

In [2]:
%load_ext memprofiler

## ironArray

In [3]:
%%mprof_run
ia.set_config_defaults(dtype=np.float64)
nrows = 100_000 # number of rows in matrix am
ncols = 25000   # number of columns in first matrix
ncols2 = 1000   # number of columns in second matrix

shape = (nrows, ncols, ncols2)
amshape = (shape[0], shape[1])
bmshape = (shape[1], shape[2])
# Obtain optimal chunk and block shapes
mparams = ia.matmul_params(amshape, bmshape)
amchunks, amblocks, bmchunks, bmblocks = mparams

filename = "../tutorials/arr-gemm.iarr"
if os.path.exists(filename):
    am = ia.open(filename)
else: 
    # btune does not represent an advantage when the number of chunks is small
    ia.set_config_defaults(btune=False)
    am = ia.random.normal(amshape, 3, 2, chunks=amchunks, blocks=amblocks, urlpath=filename, fp_mantissa_bits=20)
print(am.info)

w = np.ones(bmshape)
bm = ia.numpy2iarray(w, chunks=bmchunks, blocks=bmblocks)
print(bm.info)

type   : IArray
shape  : (100000, 25000)
chunks : (4160, 4160)
blocks : (104, 104)
cratio : 2.71

type   : IArray
shape  : (25000, 1000)
chunks : (4160, 1040)
blocks : (104, 104)
cratio : 292.60

memprofiler: used 194.90 MiB RAM (peak of 225.75 MiB) in 0.0925 s, total RAM usage 426.92 MiB


Before proceeding, let’s evict the just created file from the OS page cache, so as to better assess an actual out of core evaluation from disk.

In [4]:
!vmtouch -e $filename

           Files: 1
     Directories: 0
   Evicted Pages: 2185047 (8G)
         Elapsed: 1.8e-05 seconds


In [5]:
%%mprof_run 1.iarray::matmul
iacm_opt = ia.matmul(am, bm)
print(iacm_opt.info)

type   : IArray
shape  : (100000, 1000)
chunks : (4160, 1040)
blocks : (104, 104)
cratio : 27.03

memprofiler: used 69.56 MiB RAM (peak of 71.00 MiB) in 13.4067 s, total RAM usage 496.66 MiB


## Zarr

In [6]:
zfilename = "arr-gemm.zarr"
if not os.path.exists(zfilename):
    # Matrix zam goes to disk
    zam = zarr.empty(store=zfilename, shape=amshape)
    am.copyto(zam)
zam = zarr.open(zfilename)
print(zam.info)
dask_a = da.from_zarr(zam)

zbm = zarr.create(shape=bmshape)
bm.copyto(zbm)
print(zbm.info)
dask_b = da.from_zarr(zbm)

Type               : zarr.core.Array
Data type          : float64
Shape              : (100000, 25000)
Chunk shape        : (1563, 391)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : zarr.storage.DirectoryStore
No. bytes          : 20000000000 (18.6G)
No. bytes stored   : 7010162492 (6.5G)
Storage ratio      : 2.9
Chunks initialized : 4096/4096

Type               : zarr.core.Array
Data type          : float64
Shape              : (25000, 1000)
Chunk shape        : (1563, 125)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : zarr.storage.KVStore
No. bytes          : 200000000 (190.7M)
No. bytes stored   : 805393 (786.5K)
Storage ratio      : 248.3
Chunks initialized : 128/128



In [7]:
!vmtouch -e $zfilename

           Files: 4097
     Directories: 1
   Evicted Pages: 1713525 (6G)
         Elapsed: 0.50685 seconds


In [8]:
%%mprof_run 2.zarr::matmul
res = da.matmul(dask_a, dask_b)
cshape = (zam.shape[0], zbm.shape[1])
c = zarr.create(shape=cshape)
da.to_zarr(res, c)
print(c.info)

Type               : zarr.core.Array
Data type          : float64
Shape              : (100000, 1000)
Chunk shape        : (3125, 63)
Order              : C
Read-only          : False
Compressor         : Blosc(cname='lz4', clevel=5, shuffle=SHUFFLE, blocksize=0)
Store type         : zarr.storage.KVStore
No. bytes          : 800000000 (762.9M)
No. bytes stored   : 41116957 (39.2M)
Storage ratio      : 19.5
Chunks initialized : 512/512

memprofiler: used 7650.39 MiB RAM (peak of 22888.53 MiB) in 91.3642 s, total RAM usage 8167.45 MiB


In [9]:
!vmtouch -e $zfilename
del res
del dask_a
del zam
del dask_b
del zbm
del c
del w

           Files: 4097
     Directories: 1
   Evicted Pages: 1713525 (6G)
         Elapsed: 0.12987 seconds


## HDF5

In [10]:
ah5_urlpath = "arr-gemm.hdf5"
if not os.path.exists(ah5_urlpath):
    with h5py.File(ah5_urlpath, "w") as f:
        ah5 = f.create_dataset("arr-gemm", am.shape, dtype=am.dtype, **h5plugin.Blosc())
        am.copyto(ah5)
        
h5_file = h5py.File(ah5_urlpath, "r")
a_h5_disk = h5_file['arr-gemm']
a_h5dask = da.from_array(a_h5_disk)

bh5_urlpath = "barr-gemm.hdf5"
if not os.path.exists(bh5_urlpath):
    with h5py.File(bh5_urlpath, "w") as f:
        bh5 = f.create_dataset("barr-gemm", bm.shape, dtype=bm.dtype, **h5plugin.Blosc())
        bm.copyto(bh5)
        
h5_bfile = h5py.File(bh5_urlpath, "r", driver='core', backing_store=False)
b_h5 = h5_bfile['barr-gemm']
b_h5dask = da.from_array(b_h5)

In [11]:
!vmtouch -e $ah5_urlpath

           Files: 1
     Directories: 0
   Evicted Pages: 2197301 (8G)
         Elapsed: 0.526 seconds


In [12]:
%%mprof_run 3.hdf5::matmul
res_h5dask = da.matmul(a_h5dask, b_h5dask)

f = h5py.File("matmul.hdf5", "w", driver='core', backing_store=False)
h5_matmul = f.create_dataset(name="matmul.hdf5", shape=iacm_opt.shape, dtype=iacm_opt.dtype, **h5plugin.Blosc())
da.to_hdf5("matmul.hdf5", '/x', res_h5dask)

memprofiler: used 29.38 MiB RAM (peak of 4018.36 MiB) in 30.1175 s, total RAM usage 7469.76 MiB


In [13]:
!vmtouch -e $ah5_urlpath
del res_h5dask
del a_h5dask
del b_h5dask
del b_h5
del a_h5_disk
del h5_matmul

           Files: 1
     Directories: 0
   Evicted Pages: 2197301 (8G)
         Elapsed: 0.23848 seconds


## TileDB

In [14]:
adom = tiledb.Domain(
        tiledb.Dim(name="rows", domain=(0, amshape[0] - 1), dtype=np.int32, tile=amchunks[0] if amchunks[0]%amshape[0] == 0 else amchunks[0]%amshape[0]),
        tiledb.Dim(name="cols", domain=(0, amshape[1] - 1), dtype=np.int32, tile=amchunks[1] if amchunks[1]%amshape[1] == 0 else amchunks[1]%amshape[1]),
    )

# The array will be dense with a single attribute "a" so each (i,j) cell can store an integer.
filters = tiledb.FilterList([tiledb.ByteShuffleFilter(), tiledb.LZ4Filter(5)])
# The array will be dense with a single attribute "a" so each (i,j) cell can store an integer.
schema = tiledb.ArraySchema(
    domain=adom,  sparse=False, attrs=[tiledb.Attr(name="a", dtype=np.float64, filters=filters)]
)

# Create the (empty) array on disk.
array_name = "tiledb_a"

if not os.path.exists(array_name):
    tiledb.DenseArray.create(array_name, schema)
    with tiledb.DenseArray(array_name, mode="w") as A:
        A[:] = am.data
        
tilea = da.from_tiledb(array_name, attribute='a')

bdom = tiledb.Domain(
        tiledb.Dim(name="rows", domain=(0, bmshape[0] - 1), dtype=np.int32, tile=bmchunks[0]%bmshape[0]),
        tiledb.Dim(name="cols", domain=(0, bmshape[1] - 1), dtype=np.int32, tile=bmchunks[1]%bmshape[1]),
)

# The array will be dense with a single attribute "a" so each (i,j) cell can store an integer.
schemab = tiledb.ArraySchema(
    domain=bdom, sparse=False, attrs=[tiledb.Attr(name="b", dtype=np.float64, filters=filters)]
)

# Create the (empty) array in memory
array_nameb = "mem://tiledb_b"
tiledb.DenseArray.create(array_nameb, schemab)
with tiledb.DenseArray(array_nameb, mode="w") as B:
    B[:] = bm.data

tileb = da.from_tiledb(array_nameb, attribute='b')

In [15]:
!vmtouch -e $array_name

           Files: 4
     Directories: 7
   Evicted Pages: 2212830 (8G)
         Elapsed: 0.14367 seconds


In [16]:
%%mprof_run 4.tiledb::matmul
res_dask = da.matmul(tilea, tileb)
res_dask.to_tiledb("mem://res_tiledb")

/home/marta/miniconda3/lib/python3.9/site-packages/dask/array/routines.py:446: PerformanceWarning: Increasing number of chunks by factor of 25
  out = blockwise(


memprofiler: used 1212.71 MiB RAM (peak of 2619.27 MiB) in 478.8189 s, total RAM usage 1378.77 MiB


In [17]:
del res_dask
del tilea
del tileb 
tiledb.remove(array_nameb)

## NumPy

In [18]:
npa = am.data
npb = bm.data

In [19]:
%%mprof_run 5.numpy::matmul
npcm = np.matmul(npa, npb)

memprofiler: used 949.59 MiB RAM (peak of 949.59 MiB) in 15.4494 s, total RAM usage 21448.42 MiB


In [20]:
del npa
del npb
del npcm

## Results

In [21]:
%mprof_plot .*::matmul -t "Matrix multiplication computation"


In this summary plot we can see how:

1. ironArray (with optimized chunk and block shapes) uses *much less* memory than any other method.
2. ironArray (with optimized chunk and block shapes) is faster than any other method.

Of course, we could have spent more time optimizing for Zarr, TileDB and HDF5 optimal values by hand, but the point is that ironArray is providing a function for automatically providing chunks and blocks that are optimized for matrix multiplications, while this is something that is not implemented in neither Zarr, TileDB, HDF5 nor Dask, so this is why we went with default for them.

Finally, the fact that ironArray can be (marginally) faster than NumPy (using MKL) might be due to the fact that MKL is not too well optimized to run on AMD processors (as is the case here).


